In [3]:
import pygame
import cv2
import numpy as np
import math

In [4]:
## List of methods to be used
def is_in_rect(x,y,p1,p4):
    f1 = y - p1[1]
    f2 = y - p4[1]
    f3 = x - p1[0]
    f4 = x - p4[0]
    if f1 >= 0 and f2 <= 0 and f3 >= 0 and f4 <=0:
        return True

def is_in_circle(x,y,h,k,r):
    f5 = (x-h)**2 + (y-k)**2 - r**2
    if f5 <= 0:
        return True

def is_in_ellipse(x,y,a,b,h,k):
    f6 = ((x-h)**2)/a**2 + ((y-k)**2)/b**2 - 1
    if f6 <= 0:
        return True

def get_line_equation(x,y,p1,p2):
    if p2[0] - p1[0] != 0:
        m = (p2[1] - p1[1]) / (p2[0] - p1[0])
        f = y - p1[1] - m * x + m * p1[0]
    else:
        f = x - p2[0]
    return f

def is_poly(x,y,scale):
    in_poly1 = False
    in_poly2 = False
    in_poly3 = False
    p1 = [125*scale,94*scale]
    p2 = [163*scale,98*scale]
    p3 = [150*scale,135*scale]
    # Equation of half planes for poly one
    f7 = get_line_equation(x,y,p1,p2)
    f8 = get_line_equation(x,y,p2,p3)
    f9 = get_line_equation(x,y,p1,p3)            
    if f7 >= 0 and f8 <= 0 and f9 <=0:
        in_poly1 = True
    
    p1 = [150*scale,135*scale]
    p2 = [163*scale,98*scale]
    p3 = [163*scale,135*scale]
    # Equation of half planes for poly two
    f10 = get_line_equation(x,y,p1,p2)
    f11 = get_line_equation(x,y,p2,p3)
    f12 = get_line_equation(x,y,p1,p3)            
    if f10 >= 0 and f11 <= 0 and f12 <=0:
        in_poly2 = True
    
    p1 = [163*scale,135*scale]
    p2 = [163*scale,98*scale]
    p3 = [170*scale,60*scale]
    p4 = [193*scale,98*scale]
    p5 = [173*scale,135*scale]
    # Equation of half planes for poly three
    f13 = get_line_equation(x,y,p1,p2)
    f14 = get_line_equation(x,y,p2,p3)
    f15 = get_line_equation(x,y,p3,p4)
    f16 = get_line_equation(x,y,p4,p5)
    f17 = get_line_equation(x,y,p5,p1)
    if f13>=0 and f14>=0 and f15>=0 and f16<=0 and f17<=0:
        in_poly3 = True
        
    return in_poly1 or in_poly2 or in_poly3
    
# Draw obstacles using obstacle points on pygame surface
def draw_obstacles(obstacle_set):
    for p in obstacle_set:
        pxarray[p[0], p[1]] = pygame.Color(0, 0, 0)
        pygame.display.update()

        
def draw_obstacles_bg(img,obstacle_set):
    for p in obstacle_set:
        img[p[1],p[0]] = 0
        
### Apply minkowski sum to obstacle points 
def minkowski_sum(bg,r,obstacle_set,width,height):
    new_obstacle_set = set()
    for p in obstacle_set:
        h = p[0]
        k = p[1]
        # skip convolution for pixels that are completely inside the circle
        if bg[k,h-r] == 0 and bg[k,h+r] == 0 and bg[k-r,h] == 0 and bg[k+r,h] == 0:
            continue
        for x in range(h-r,h+r):
            for y in range(k-r,k+r):
                if x < 0 or x >= width or y < 0 or y >= height:
                    continue
                else:
                    f = (x-h)**2 + (y-k)**2 - r**2
                    if f <= 0:
                        new_obstacle_set.add((x,y))
                    
    return new_obstacle_set
    # using each point find new obstacle points
    # don't forget to delete the old one

In [10]:
class Node:
    def __init__(self):
        self.visited = False
        self.cost = 999999
        self.neighbours = {}
        self.prev = None
        
class Graph:
    # graph constructor that creates an empty dictionary
    # nodes = {(x,y):Node} where x,y are coordinates of node
    def __init__(self):
        self.nodes = {}
    # loop through image and create node object for each pixel
    def create_nodes(self,width,height,obstacle_set):
        for x in range(0,width):
            for y in range(0,height):
                if (x,y) not in obstacle_set:
                    self.nodes[(x,y)] = Node()
    # for given pixel and find it's neighbours
    def calculate_neighbours(self,node_tuple,width,height):
        x = node_tuple[0]
        y = node_tuple[1]
        dig = 1.41
        strght = 1
        if (x-1,y-1) not in obstacle_set and x-1  >= 0 and y-1 >= 0:
            self.nodes[(x,y)].neighbours[(x-1,y-1)] = dig
        if (x,y-1) not in obstacle_set and y-1 >= 0:
            self.nodes[(x,y)].neighbours[(x,y-1)] = strght
        if (x+1,y-1) not in obstacle_set and x+1 < width:
            self.nodes[(x,y)].neighbours[(x+1,y-1)] = dig
        if (x-1,y) not in obstacle_set and x-1 >= 0:
            self.nodes[(x,y)].neighbours[(x-1,y)] = strght
        if (x+1,y) not in obstacle_set and x+1 < width:
            self.nodes[(x,y)].neighbours[(x+1,y)] = strght
        if (x-1,y+1) not in obstacle_set and x-1 >= 0 and y+1 < height:
            self.nodes[(x,y)].neighbours[(x-1,y+1)] = dig
        if (x,y+1) not in obstacle_set and y+1 < height:
            self.nodes[(x,y)].neighbours[(x,y+1)] = strght
        if (x+1,y+1) not in obstacle_set and x+1 < width and y+1 < height:
            self.nodes[(x,y)].neighbours[(x+1,y+1)] = dig

In [11]:
import time
# scale the window size
scale = 1
height = 150*scale
width = 250*scale

# create a background image
bg = np.zeros((height,width,3),dtype=np.uint8)
for x in range(0,bg.shape[0]):
    for y in range(0,bg.shape[1]):
        bg[x,y] = (255,255,255)

# Define obstacle point x and y set
obstacle_set = set()

# iterate for each pixel and find out if it is an obstacle
# if it is in the obstacle store it in the obstacle set
for x in range(0,width):
    for y in range(0,height):
        if is_in_rect(x,y,[50*scale,38*scale],[100*scale,83*scale]) or is_in_circle(x,y,190*scale,20*scale,15*scale) or is_in_ellipse(x,y,30*scale,12*scale,140*scale,30*scale) or is_poly(x,y,scale):
            obstacle_set.add((x,y))
            bg[y,x] = (0,0,0)  

# Calculate Mikowski space
#r = 10
#obstacle_set = minkowski_sum(bg,r*scale,obstacle_set,width,height)
draw_obstacles_bg(bg,obstacle_set)
cv2.imwrite("background_no_min.png",bg)

graph = Graph()
graph.create_nodes(width,height,obstacle_set)
for node in graph.nodes:
    graph.calculate_neighbours(node,width,height)
#for key,value in graph.nodes.items():
#    print(key,": ",value.neighbours)

# define color for visited node
green = (60,179,113)
# define color for unvisited node
grey = (192,192,192)
for node in graph.nodes:
        if graph.nodes[node].visited == False:
            bg[node[1],node[0]] = grey
        else:
            bg[node[1],node[0]] = green
            
        #print(node,": ",graph.nodes[node].neighbours)
            
            
            
# Take user input
    
# 

cv2.imshow("image",bg)
cv2.waitKey(0)
cv2.destroyAllWindows()

(231, 78) :  {(232, 78): 1, (232, 77): 1.41, (231, 79): 1, (230, 77): 1.41, (231, 77): 1, (230, 79): 1.41, (232, 79): 1.41, (230, 78): 1}
(238, 115) :  {(237, 114): 1.41, (239, 114): 1.41, (237, 115): 1, (239, 116): 1.41, (239, 115): 1, (237, 116): 1.41, (238, 114): 1, (238, 116): 1}
(57, 15) :  {(58, 15): 1, (56, 14): 1.41, (57, 16): 1, (58, 14): 1.41, (57, 14): 1, (58, 16): 1.41, (56, 16): 1.41, (56, 15): 1}
(80, 125) :  {(79, 124): 1.41, (79, 125): 1, (81, 124): 1.41, (80, 126): 1, (81, 125): 1, (79, 126): 1.41, (81, 126): 1.41, (80, 124): 1}
(43, 3) :  {(44, 2): 1.41, (44, 4): 1.41, (43, 4): 1, (42, 4): 1.41, (43, 2): 1, (42, 3): 1, (44, 3): 1, (42, 2): 1.41}
(185, 66) :  {(184, 67): 1.41, (185, 65): 1, (186, 65): 1.41, (184, 65): 1.41, (185, 67): 1, (186, 67): 1.41, (184, 66): 1, (186, 66): 1}
(29, 44) :  {(30, 43): 1.41, (30, 44): 1, (29, 45): 1, (28, 43): 1.41, (28, 45): 1.41, (28, 44): 1, (30, 45): 1.41, (29, 43): 1}
(67, 137) :  {(67, 136): 1, (68, 138): 1.41, (68, 137): 1, (6

(3, 110) :  {(4, 109): 1.41, (3, 111): 1, (2, 109): 1.41, (3, 109): 1, (2, 111): 1.41, (4, 111): 1.41, (2, 110): 1, (4, 110): 1}
(70, 124) :  {(71, 124): 1, (70, 125): 1, (69, 123): 1.41, (70, 123): 1, (71, 123): 1.41, (69, 124): 1, (71, 125): 1.41, (69, 125): 1.41}
(57, 21) :  {(58, 21): 1, (57, 22): 1, (58, 20): 1.41, (57, 20): 1, (56, 22): 1.41, (58, 22): 1.41, (56, 21): 1, (56, 20): 1.41}
(20, 143) :  {(21, 142): 1.41, (19, 143): 1, (21, 143): 1, (21, 144): 1.41, (19, 144): 1.41, (20, 142): 1, (19, 142): 1.41, (20, 144): 1}
(198, 65) :  {(198, 66): 1, (199, 64): 1.41, (197, 64): 1.41, (199, 65): 1, (197, 65): 1, (197, 66): 1.41, (198, 64): 1, (199, 66): 1.41}
(43, 38) :  {(44, 37): 1.41, (43, 39): 1, (42, 37): 1.41, (43, 37): 1, (42, 39): 1.41, (44, 39): 1.41, (42, 38): 1, (44, 38): 1}
(249, 33) :  {(248, 33): 1, (249, 34): 1, (249, 32): 1, (248, 32): 1.41, (248, 34): 1.41}
(29, 71) :  {(29, 70): 1, (29, 72): 1, (28, 71): 1, (28, 72): 1.41, (30, 71): 1, (28, 70): 1.41, (30, 72): 1.

(47, 19) :  {(47, 20): 1, (47, 18): 1, (48, 20): 1.41, (46, 19): 1, (46, 20): 1.41, (48, 19): 1, (46, 18): 1.41, (48, 18): 1.41}
(239, 49) :  {(240, 49): 1, (238, 49): 1, (240, 48): 1.41, (238, 48): 1.41, (239, 50): 1, (238, 50): 1.41, (239, 48): 1, (240, 50): 1.41}
(218, 63) :  {(219, 64): 1.41, (217, 64): 1.41, (218, 62): 1, (217, 62): 1.41, (219, 62): 1.41, (217, 63): 1, (219, 63): 1, (218, 64): 1}
(215, 86) :  {(215, 85): 1, (214, 87): 1.41, (216, 87): 1.41, (214, 86): 1, (216, 86): 1, (216, 85): 1.41, (215, 87): 1, (214, 85): 1.41}
(17, 36) :  {(17, 37): 1, (17, 35): 1, (18, 35): 1.41, (16, 36): 1, (18, 37): 1.41, (16, 37): 1.41, (16, 35): 1.41, (18, 36): 1}
(10, 84) :  {(10, 85): 1, (11, 84): 1, (9, 84): 1, (11, 85): 1.41, (9, 85): 1.41, (9, 83): 1.41, (10, 83): 1, (11, 83): 1.41}
(94, 26) :  {(94, 27): 1, (95, 27): 1.41, (95, 25): 1.41, (93, 25): 1.41, (94, 25): 1, (93, 26): 1, (95, 26): 1, (93, 27): 1.41}
(131, 44) :  {(132, 45): 1.41, (130, 45): 1.41, (132, 44): 1, (130, 44): 

(54, 91) :  {(53, 90): 1.41, (55, 90): 1.41, (53, 91): 1, (55, 92): 1.41, (55, 91): 1, (53, 92): 1.41, (54, 90): 1, (54, 92): 1}
(1, 77) :  {(1, 78): 1, (2, 77): 1, (2, 76): 1.41, (1, 76): 1, (0, 78): 1.41, (2, 78): 1.41, (0, 77): 1, (0, 76): 1.41}
(115, 91) :  {(116, 90): 1.41, (116, 92): 1.41, (115, 92): 1, (114, 92): 1.41, (115, 90): 1, (114, 91): 1, (116, 91): 1, (114, 90): 1.41}
(243, 14) :  {(244, 13): 1.41, (243, 15): 1, (242, 13): 1.41, (243, 13): 1, (242, 15): 1.41, (244, 15): 1.41, (242, 14): 1, (244, 14): 1}
(10, 149) :  {(9, 149): 1, (11, 148): 1.41, (10, 148): 1, (9, 148): 1.41, (11, 149): 1}
(48, 32) :  {(48, 33): 1, (48, 31): 1, (49, 33): 1.41, (49, 32): 1, (47, 33): 1.41, (47, 32): 1, (47, 31): 1.41, (49, 31): 1.41}
(34, 15) :  {(35, 15): 1, (34, 16): 1, (35, 16): 1.41, (33, 16): 1.41, (34, 14): 1, (33, 14): 1.41, (35, 14): 1.41, (33, 15): 1}
(162, 56) :  {(162, 55): 1, (163, 56): 1, (161, 56): 1, (163, 57): 1.41, (161, 57): 1.41, (162, 57): 1, (161, 55): 1.41, (163, 55

(142, 77) :  {(143, 76): 1.41, (142, 76): 1, (141, 76): 1.41, (143, 77): 1, (141, 77): 1, (142, 78): 1, (141, 78): 1.41, (143, 78): 1.41}
(180, 128) :  {(179, 127): 1.41, (181, 127): 1.41, (181, 128): 1, (179, 128): 1, (181, 129): 1.41, (180, 127): 1, (179, 129): 1.41, (180, 129): 1}
(75, 90) :  {(74, 91): 1.41, (75, 91): 1, (76, 91): 1.41, (74, 90): 1, (76, 90): 1, (75, 89): 1, (76, 89): 1.41, (74, 89): 1.41}
(38, 34) :  {(38, 35): 1, (39, 35): 1.41, (39, 33): 1.41, (37, 33): 1.41, (38, 33): 1, (37, 34): 1, (39, 34): 1, (37, 35): 1.41}
(35, 126) :  {(36, 125): 1.41, (35, 127): 1, (34, 125): 1.41, (35, 125): 1, (34, 127): 1.41, (36, 127): 1.41, (34, 126): 1, (36, 126): 1}
(8, 17) :  {(9, 16): 1.41, (7, 16): 1.41, (9, 17): 1, (7, 17): 1, (9, 18): 1.41, (8, 16): 1, (7, 18): 1.41, (8, 18): 1}
(227, 103) :  {(226, 103): 1, (227, 104): 1, (228, 103): 1, (226, 102): 1.41, (228, 102): 1.41, (227, 102): 1, (228, 104): 1.41, (226, 104): 1.41}
(33, 74) :  {(32, 75): 1.41, (32, 74): 1, (33, 73): 

...

(2, 15) :  {(3, 15): 1, (2, 16): 1, (3, 16): 1.41, (1, 16): 1.41, (2, 14): 1, (1, 14): 1.41, (3, 14): 1.41, (1, 15): 1}
(215, 130) :  {(214, 131): 1.41, (215, 131): 1, (216, 131): 1.41, (214, 130): 1, (216, 130): 1, (215, 129): 1, (216, 129): 1.41, (214, 129): 1.41}
(153, 137) :  {(152, 137): 1, (154, 136): 1.41, (152, 136): 1.41, (154, 138): 1.41, (153, 136): 1, (152, 138): 1.41, (154, 137): 1, (153, 138): 1}
(190, 91) :  {(191, 92): 1.41, (191, 91): 1, (190, 90): 1, (190, 92): 1, (189, 90): 1.41, (191, 90): 1.41, (189, 91): 1}
(177, 51) :  {(177, 50): 1, (178, 51): 1, (178, 50): 1.41, (176, 51): 1, (176, 52): 1.41, (176, 50): 1.41, (177, 52): 1, (178, 52): 1.41}
(137, 45) :  {(136, 46): 1.41, (138, 46): 1.41, (136, 45): 1, (136, 44): 1.41, (137, 46): 1, (138, 45): 1, (138, 44): 1.41, (137, 44): 1}
(163, 96) :  {(162, 95): 1.41, (163, 95): 1, (163, 97): 1, (162, 97): 1.41, (162, 96): 1}
(21, 130) :  {(22, 131): 1.41, (22, 130): 1, (20, 131): 1.41, (20, 130): 1, (21, 129): 1, (22, 129)

(208, 25) :  {(209, 24): 1.41, (207, 24): 1.41, (209, 25): 1, (207, 25): 1, (209, 26): 1.41, (208, 24): 1, (207, 26): 1.41, (208, 26): 1}
(119, 6) :  {(119, 5): 1, (118, 7): 1.41, (120, 7): 1.41, (118, 6): 1, (120, 6): 1, (120, 5): 1.41, (119, 7): 1, (118, 5): 1.41}
(156, 12) :  {(157, 13): 1.41, (157, 12): 1, (155, 11): 1.41, (156, 11): 1, (156, 13): 1, (155, 13): 1.41, (155, 12): 1, (157, 11): 1.41}
(45, 20) :  {(44, 21): 1.41, (44, 20): 1, (46, 21): 1.41, (45, 19): 1, (46, 19): 1.41, (46, 20): 1, (45, 21): 1, (44, 19): 1.41}
(29, 103) :  {(29, 102): 1, (30, 104): 1.41, (29, 104): 1, (28, 103): 1, (28, 104): 1.41, (30, 103): 1, (28, 102): 1.41, (30, 102): 1.41}
(142, 75) :  {(143, 76): 1.41, (143, 75): 1, (141, 76): 1.41, (142, 74): 1, (142, 76): 1, (141, 74): 1.41, (143, 74): 1.41, (141, 75): 1}
(38, 40) :  {(37, 41): 1.41, (38, 41): 1, (38, 39): 1, (37, 39): 1.41, (39, 40): 1, (39, 39): 1.41, (37, 40): 1, (39, 41): 1.41}
(126, 60) :  {(126, 59): 1, (127, 59): 1.41, (125, 60): 1, (1

(95, 113) :  {(96, 113): 1, (94, 113): 1, (96, 112): 1.41, (94, 112): 1.41, (95, 114): 1, (94, 114): 1.41, (95, 112): 1, (96, 114): 1.41}
(116, 46) :  {(116, 45): 1, (117, 46): 1, (115, 47): 1.41, (115, 45): 1.41, (117, 47): 1.41, (116, 47): 1, (117, 45): 1.41, (115, 46): 1}
(153, 92) :  {(153, 93): 1, (153, 91): 1, (154, 91): 1.41, (154, 93): 1.41, (152, 92): 1, (152, 93): 1.41, (152, 91): 1.41, (154, 92): 1}
(132, 13) :  {(133, 14): 1.41, (132, 12): 1, (131, 12): 1.41, (131, 13): 1, (133, 12): 1.41, (133, 13): 1, (131, 14): 1.41, (132, 14): 1}
(102, 73) :  {(101, 73): 1, (101, 74): 1.41, (102, 72): 1, (103, 74): 1.41, (102, 74): 1, (103, 72): 1.41, (101, 72): 1.41, (103, 73): 1}
(49, 83) :  {(49, 82): 1, (48, 84): 1.41, (48, 83): 1, (48, 82): 1.41, (49, 84): 1, (50, 84): 1.41}
(72, 140) :  {(73, 141): 1.41, (73, 139): 1.41, (72, 141): 1, (71, 140): 1, (71, 139): 1.41, (72, 139): 1, (71, 141): 1.41, (73, 140): 1}
(126, 67) :  {(125, 66): 1.41, (127, 66): 1.41, (125, 67): 1, (127, 68):

(65, 96) :  {(64, 97): 1.41, (66, 96): 1, (64, 96): 1, (64, 95): 1.41, (66, 95): 1.41, (65, 97): 1, (66, 97): 1.41, (65, 95): 1}
(28, 108) :  {(29, 108): 1, (27, 107): 1.41, (28, 107): 1, (28, 109): 1, (27, 109): 1.41, (27, 108): 1, (29, 109): 1.41, (29, 107): 1.41}
(156, 89) :  {(155, 90): 1.41, (157, 88): 1.41, (156, 90): 1, (155, 88): 1.41, (157, 89): 1, (155, 89): 1, (157, 90): 1.41, (156, 88): 1}
(219, 43) :  {(219, 42): 1, (218, 43): 1, (220, 43): 1, (218, 42): 1.41, (220, 42): 1.41, (220, 44): 1.41, (219, 44): 1, (218, 44): 1.41}
(89, 106) :  {(88, 105): 1.41, (89, 107): 1, (90, 107): 1.41, (90, 106): 1, (88, 107): 1.41, (89, 105): 1, (90, 105): 1.41, (88, 106): 1}
(217, 93) :  {(216, 94): 1.41, (218, 94): 1.41, (216, 93): 1, (216, 92): 1.41, (217, 94): 1, (218, 93): 1, (218, 92): 1.41, (217, 92): 1}
(234, 6) :  {(235, 7): 1.41, (234, 5): 1, (235, 5): 1.41, (234, 7): 1, (233, 5): 1.41, (233, 6): 1, (235, 6): 1, (233, 7): 1.41}
(75, 11) :  {(75, 10): 1, (74, 11): 1, (76, 11): 1, 

(115, 50) :  {(114, 51): 1.41, (115, 51): 1, (116, 51): 1.41, (114, 50): 1, (116, 50): 1, (115, 49): 1, (116, 49): 1.41, (114, 49): 1.41}
(13, 95) :  {(12, 95): 1, (14, 95): 1, (12, 94): 1.41, (14, 94): 1.41, (13, 94): 1, (12, 96): 1.41, (13, 96): 1, (14, 96): 1.41}
(245, 64) :  {(245, 63): 1, (245, 65): 1, (244, 65): 1.41, (244, 63): 1.41, (246, 63): 1.41, (246, 64): 1, (246, 65): 1.41, (244, 64): 1}
(10, 138) :  {(9, 138): 1, (11, 138): 1, (9, 139): 1.41, (10, 139): 1, (11, 139): 1.41, (11, 137): 1.41, (9, 137): 1.41, (10, 137): 1}
(138, 71) :  {(139, 71): 1, (138, 72): 1, (139, 72): 1.41, (137, 72): 1.41, (138, 70): 1, (137, 70): 1.41, (139, 70): 1.41, (137, 71): 1}
(192, 116) :  {(193, 117): 1.41, (193, 115): 1.41, (192, 117): 1, (191, 116): 1, (191, 115): 1.41, (192, 115): 1, (191, 117): 1.41, (193, 116): 1}
(3, 114) :  {(2, 115): 1.41, (3, 115): 1, (4, 115): 1.41, (2, 114): 1, (4, 114): 1, (3, 113): 1, (4, 113): 1.41, (2, 113): 1.41}
(162, 65) :  {(161, 66): 1.41, (162, 64): 1, (

In [22]:
a = list(input('Please enter two numbers'))
print(a)

Please enter two numbers2 3 4 5
['2', ' ', '3', ' ', '4', ' ', '5']
